In [1]:
# Dependencies
import hvplot.pandas
import holoviews as hv
import pandas as pd
from pathlib import Path
import numpy as np
from configfg import DATAWAGOV_KEY

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Load the dataset from API
url = "https://data.wa.gov/api/views/f6w7-q2d2/rows.csv?accessType=DOWNLOAD"
ev_df = pd.read_csv(url)

# Inspect the dataset structure
ev_df.head()

VIN (1-10)     County       City State  Postal Code  Model Year     Make  \
0  5UXTA6C0XM     Kitsap    Seabeck    WA      98380.0        2021      BMW   
1  5YJ3E1EB1J     Kitsap    Poulsbo    WA      98370.0        2018    TESLA   
2  WP0AD2A73G  Snohomish    Bothell    WA      98012.0        2016  PORSCHE   
3  5YJ3E1EB5J     Kitsap  Bremerton    WA      98310.0        2018    TESLA   
4  1N4AZ1CP3K       King    Redmond    WA      98052.0        2019   NISSAN   

      Model                   Electric Vehicle Type  \
0        X5  Plug-in Hybrid Electric Vehicle (PHEV)   
1   MODEL 3          Battery Electric Vehicle (BEV)   
2  PANAMERA  Plug-in Hybrid Electric Vehicle (PHEV)   
3   MODEL 3          Battery Electric Vehicle (BEV)   
4      LEAF          Battery Electric Vehicle (BEV)   

  Clean Alternative Fuel Vehicle (CAFV) Eligibility  Electric Range  \
0           Clean Alternative Fuel Vehicle Eligible            30.0   
1           Clean Alternative Fuel Vehicle Eligible           215.0   
2             Not eligible due to low battery range            15.0   
3           Clean Alternative Fuel Vehicle Eligible           215.0   
4           Clean Alternative Fuel Vehicle Eligible           150.0   

   Base MSRP  Legislative District  DOL Vehicle ID  \
0        0.0                  35.0       267929112   
1        0.0                  23.0       475911439   
2        0.0                   1.0       101971278   
3        0.0                  23.0       474363746   
4        0.0                  45.0       476346482   

                  Vehicle Location  \
0  POINT (-122.8728334 47.5798304)   
1  POINT (-122.6368884 47.7469547)   
2    POINT (-122.206146 47.839957)   
3  POINT (-122.6231895 47.5930874)   
4      POINT (-122.13158 47.67858)   

                                Electric Utility  2020 Census Tract  
0                         PUGET SOUND ENERGY INC       5.303509e+10  
1                         PUGET SOUND ENERGY INC       5.303509e+10  
2                         PUGET SOUND ENERGY INC       5.306105e+10  
3                         PUGET SOUND ENERGY INC       5.303508e+10  
4  PUGET SOUND ENERGY INC||CITY OF TACOMA - (WA)       5.303303e+10

In [2]:
# Get a list of all of our columns for easy reference
ev_df.columns

Index(['VIN (1-10)', 'County', 'City', 'State', 'Postal Code', 'Model Year',
       'Make', 'Model', 'Electric Vehicle Type',
       'Clean Alternative Fuel Vehicle (CAFV) Eligibility', 'Electric Range',
       'Base MSRP', 'Legislative District', 'DOL Vehicle ID',
       'Vehicle Location', 'Electric Utility', '2020 Census Tract'],
      dtype='object')

In [3]:
# Extract "VIN", "County", and "Vehicle Location"
ev_df_red = ev_df.loc[:, ["VIN (1-10)", "State", "County", "Vehicle Location"]]
ev_df_red.count()

VIN (1-10)          210165
State               210165
County              210161
Vehicle Location    210155
dtype: int64

In [4]:
# Create a new DataFrame that looks into for only WA
ev_df_wa = ev_df_red.loc[ev_df_red["State"] == "WA"]
ev_df_wa.count()

VIN (1-10)          209720
State               209720
County              209720
Vehicle Location    209714
dtype: int64

In [5]:
# Rename Vehicle Location column
ev_df_wa = ev_df_wa.rename(columns={"Vehicle Location":"VehLoc"})
ev_df_wa.head()

VIN (1-10) State     County                           VehLoc
0  5UXTA6C0XM    WA     Kitsap  POINT (-122.8728334 47.5798304)
1  5YJ3E1EB1J    WA     Kitsap  POINT (-122.6368884 47.7469547)
2  WP0AD2A73G    WA  Snohomish    POINT (-122.206146 47.839957)
3  5YJ3E1EB5J    WA     Kitsap  POINT (-122.6231895 47.5930874)
4  1N4AZ1CP3K    WA       King      POINT (-122.13158 47.67858)

In [6]:
# Split Vehicle Location Column into two columns named "Longitude" and "Latitude"
ev_df_wa[['VehLoc','LongLat']] = ev_df_wa.VehLoc.str.split('\(|\)', expand=True).iloc[:,[0,1]]
ev_df_wa[['Longitude','Latitude']] = ev_df_wa.LongLat.str.split(' ', expand=True).iloc[:,[0,1]]

# Extract "VIN", "County", "Longitude", and "Latitude"
ev_df_coordinates = ev_df_wa.loc[:, ["VIN (1-10)", "County", "Longitude", "Latitude"]]

ev_df_coordinates.dtypes

VIN (1-10)    object
County        object
Longitude     object
Latitude      object
dtype: object

In [7]:
# Convert Longitude and Latitude columns to Float
ev_df_coordinates = ev_df_coordinates.astype({"Longitude": "float",
                                              "Latitude": "float"})
ev_df_coordinates.dtypes

VIN (1-10)     object
County         object
Longitude     float64
Latitude      float64
dtype: object

In [8]:
# Save GroupBy data to CSV to be used for Bar Graph
ev_df_coordinates.to_csv("Resources/WAEV_COUNTY_INFO.csv", index=True)

In [9]:
# Configure the map plot
map_plot = ev_df_coordinates.hvplot.points(
    "Longitude", 
    "Latitude", 
    geo = True, 
    tiles = "OSM", 
    frame_width = 1200, 
    frame_height = 600,
)

# Save Map Plot to PNG
hv.save(map_plot, 'Images/WAEV_BYCOUNTY_MAP.png', backend='bokeh')

# Display the Map Plot
map_plot

:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Points.I :Points   [Longitude,Latitude]